In [97]:
import matplotlib.pyplot as plt
import matplotlib.image as mpimg
import numpy as np
import os

import unittest

import trimesh
import math
import networkx as nx

In [26]:
base_path = os.getcwd() + "//UoY//"

# Using trimesh package

In [35]:
obj_filename = base_path + '00023-13-mww38ngngy.obj'
mesh = trimesh.load(obj_filename)

In [36]:
mesh.visual = mesh.visual.to_color()

In [37]:
for index, facet in enumerate(mesh.visual.vertex_colors):
    mesh.visual.vertex_colors[index] = [0,255,0,0]
mesh.show()

# Preprocessing - Smoothing

In [38]:
laplacian_smoothing_mesh = mesh.copy()
trimesh.smoothing.filter_laplacian(laplacian_smoothing_mesh)
laplacian_smoothing_mesh.show()

In [39]:
humphrey_smoothing_mesh = mesh.copy()
trimesh.smoothing.filter_humphrey(humphrey_smoothing_mesh)
humphrey_smoothing_mesh.show()

In [40]:
taubin_smoothing_mesh = mesh.copy()
trimesh.smoothing.filter_taubin(taubin_smoothing_mesh)
taubin_smoothing_mesh.show()

In [41]:
laplacian_calculation_smoothing_mesh = mesh.copy()
trimesh.smoothing.laplacian_calculation(laplacian_calculation_smoothing_mesh)
laplacian_calculation_smoothing_mesh.show()

In [42]:
smoothing_mesh = taubin_smoothing_mesh.copy()

# Preprocessing - Cropping

In [44]:
class CroppingFilter():
    def __init__(self):
        self.mesh = None
        self.noseIndex = 0
        self.depthSortVertices = None
        
    def InitMeshAttributes(self, mesh):
        self.mesh = mesh.copy()
        self.depthSortVertices = sorted(self.mesh.vertices, key = lambda vertice : vertice[2], reverse = True)
        
    def GetMesh(self):
        return self.mesh
    
    def GetNoseIndex(self):
        return self.noseIndex
        
    def Filtering(self, mesh, r):
        self.InitMeshAttributes(mesh)
        preSphereVerticeNum = 0
        for vertice in self.depthSortVertices:
            mesh = self.GetShpereMesh(self.mesh, vertice, r)
            mesh.show()
            curSphereVerticeNum = len(mesh.vertices)
            if curSphereVerticeNum - preSphereVerticeNum > 150:
                self.noseIndex = self.FindNoseIndex(mesh.vertices, vertice)
                self.mesh = mesh
                break
            preSphereVerticeNum = curSphereVerticeNum
        
    def GetShpereMesh(self, originMesh, centerVertice, r):
        mesh = originMesh.copy()
        sphereIndexes = self.GetSphereIndexes(mesh, centerVertice, r)
        mesh = self.RemoveFaces(mesh, sphereIndexes)
        mesh = self.RemoveVertices(mesh)
        return mesh

    def GetSphereIndexes(self, mesh, centerVertice, r):
        sphereIndexes = np.array([])
        for index, vertice in enumerate(mesh.vertices):
            if self.EuclideanDistance(centerVertice, vertice, 3) < r:
                sphereIndexes = np.append(sphereIndexes, index)
        return sphereIndexes

    def EuclideanDistance(self, lvertice, rvertice, dimensional):
        euclideanDistance = 0
        for d in range(dimensional):
            euclideanDistance += pow(lvertice[d] - rvertice[d], 2)
        euclideanDistance = math.sqrt(euclideanDistance)
        return euclideanDistance

    def RemoveFaces(self, mesh, sphereIndexes):
        faces = np.empty((0,3), int)
        for face in mesh.faces:
            if self.IsFaceCompositionOfShpereVertices(face, sphereIndexes):
                faces = np.append(faces, np.array([face]), axis=0)
        mesh.faces = faces
        return mesh

    def IsFaceCompositionOfShpereVertices(self, face, sphereIndexes):
        for vertice in face:
            if not(vertice in sphereIndexes):
                return False
        return True

    def RemoveVertices(self, mesh):
        mesh.remove_unreferenced_vertices()
        return mesh
    
    def FindNoseIndex(self, vertices, vertice):
        for index in range(len(vertices)):
            if (np.array(vertices[index]) == np.array(vertice)).all():
                return index
        return -1

In [49]:
croppingFilter = CroppingFilter()
croppingFilter.Filtering(smoothing_mesh, 125)
cropping_mesh = croppingFilter.GetMesh()
cropping_mesh.visual.vertex_colors[croppingFilter.GetNoseIndex()] = [255,0,0,0]
cropping_mesh.show()

In [194]:
class BoundaryVertex():
    def __init__(self, edges, triangles):
        self.one_ring_edges = np.array(edges)
        self.one_ring_triangles = np.array(triangles)
        
    def get_one_ring_edges(self):
        return self.one_ring_edges
    
    def get_one_ring_triangles(self):
        return self.one_ring_triangles

In [195]:
class BoundaryVertexTest(unittest.TestCase):
    @classmethod
    def setUpClass(self):
        self.boundary_vertex = BoundaryVertex(np.array([[0, 1], [0, 2], [0, 3], [0, 4], [0, 5]]), 
                                              np.array([[0, 1, 2], [0, 2, 3], [0, 3, 4], [0, 4, 5], [0, 5, 1]]))
        
    def test_if_has_5_1_ring_edges_return_edge_list(self):
        self.assertTrue(np.alltrue(self.boundary_vertex.get_one_ring_edges() == 
                                   np.array([[0, 1], [0, 2], [0, 3], [0, 4], [0, 5]])))
        
    def test_if_has_5_1_ring_triangles_return_triangle_list(self):
        self.assertTrue(np.alltrue(self.boundary_vertex.get_one_ring_triangles() == 
                                   np.array([[0, 1, 2], [0, 2, 3], [0, 3, 4], [0, 4, 5], [0, 5, 1]])))
        
unittest.main(argv=[''], verbosity=2, exit=False)

test_get_one_ring_triangles_should_get_whole_vertex_related_triangles (__main__.BoundaryVertexCheckerTest) ... ok
test_get_one_ring_vertices_should_get_whole_vertex_neighbors (__main__.BoundaryVertexCheckerTest) ... ok
test_if_vertex_is_boundary_vertex_then_should_be_true (__main__.BoundaryVertexCheckerTest) ... ok
test_if_vertex_not_boundary_vertex_then_should_be_false (__main__.BoundaryVertexCheckerTest) ... ok
test_if_has_5_1_ring_edges_return_edge_list (__main__.BoundaryVertexTest) ... ok
test_if_has_5_1_ring_triangles_return_triangle_list (__main__.BoundaryVertexTest) ... ok

----------------------------------------------------------------------
Ran 6 tests in 0.007s

OK


In [196]:
class BoundaryVertexChecker():
    def __init__(self, mesh):
        self.mesh = mesh
        self.all_one_ring_vertices = self.__get_all_one_ring_vertices(self.mesh)
        self.all_one_ring_triangles = self.__get_all_one_ring_triangles(self.mesh)
        
    def __get_all_one_ring_triangles(self, mesh):
        triangles = mesh.faces
        all_one_ring_triangles = [[] for i in range(len(mesh.vertices))]
        for triangle in triangles:
            for vertex in triangle:
                all_one_ring_triangles[vertex].append(triangle)
        return all_one_ring_triangles
        
    def __get_all_one_ring_vertices(self, mesh):
        graph = nx.from_edgelist(mesh.edges_unique)
        all_one_ring_vertices = [list(graph[i].keys()) for i in range(len(mesh.vertices))]
        return all_one_ring_vertices
        
    def is_boundary_vertex(self, vertex):
        idx_list = np.flatnonzero((self.mesh.vertices == vertex).all(1))
        idx = idx_list[0]
        return len(self.all_one_ring_vertices[idx]) != len(self.all_one_ring_triangles[idx])
        
m = trimesh.Trimesh([[-0.5, -0.5, -0.5], 
                     [-0.5, -0.5, 0.5], 
                     [-0.5, 0.5, -0.5], 
                     [-0.5, 0.5, 0.5], 
                     [ 0.5, -0.5, -0.5], 
                     [ 0.5, -0.5, 0.5], 
                     [ 0.5, 0.5, -0.5], 
                     [ 0.5, 0.5, 0.5]], 
                    [[1, 3, 0], 
                     [4, 1, 0], 
                     [0, 3, 2], 
                     [2, 4, 0], 
                     [5, 1, 4], 
                     [5, 7, 1], 
                     [3, 7, 2], 
                     [6, 4, 2], 
                     [2, 7, 6], 
                     [6, 5, 4], 
                     [7, 5, 6]])
m.vertex_neighbors

[[1, 2, 3, 4],
 [0, 3, 4, 5, 7],
 [0, 3, 4, 6, 7],
 [0, 1, 2, 7],
 [0, 1, 2, 5, 6],
 [1, 4, 6, 7],
 [2, 4, 5, 7],
 [1, 2, 3, 5, 6]]

In [197]:
class BoundaryVertexCheckerTest(unittest.TestCase):
    @classmethod
    def setUpClass(self):
        self.mesh = trimesh.Trimesh([[-0.5, -0.5, -0.5], 
                                     [-0.5, -0.5, 0.5], 
                                     [-0.5, 0.5, -0.5], 
                                     [-0.5, 0.5, 0.5], 
                                     [ 0.5, -0.5, -0.5], 
                                     [ 0.5, -0.5, 0.5], 
                                     [ 0.5, 0.5, -0.5], 
                                     [ 0.5, 0.5, 0.5]], 
                                    [[1, 3, 0], 
                                     [4, 1, 0], 
                                     [0, 3, 2], 
                                     [2, 4, 0], 
                                     [5, 1, 4], 
                                     [5, 7, 1], 
                                     [3, 7, 2], 
                                     [6, 4, 2], 
                                     [2, 7, 6], 
                                     [6, 5, 4], 
                                     [7, 5, 6]])
        self.boundary_vertex_checker = BoundaryVertexChecker(self.mesh)
        
    def test_get_one_ring_vertices_should_get_whole_vertex_neighbors(self):
        correct_one_ring_vertices = [[1, 2, 3, 4], [0, 3, 4, 5, 7], [0, 3, 4, 6, 7], [0, 1, 2, 7], 
                                     [0, 1, 2, 5, 6], [1, 4, 6, 7], [2, 4, 5, 7], [1, 2, 3, 5, 6]]
        all_one_ring_vertices = self.boundary_vertex_checker._BoundaryVertexChecker__get_all_one_ring_vertices(self.mesh)
        for idx, one_ring_vertices in enumerate(all_one_ring_vertices):
            self.assertTrue(sorted(correct_one_ring_vertices[idx]) == sorted(one_ring_vertices))
            
    def test_get_one_ring_triangles_should_get_whole_vertex_related_triangles(self):
        correct_all_one_ring_triangles = [[[1, 3, 0], [4, 1, 0], [0, 3, 2], [2, 4, 0]], 
                                          [[1, 3, 0], [4, 1, 0], [5, 1, 4], [5, 7, 1]], 
                                          [[0, 3, 2], [2, 4, 0], [3, 7, 2], [6, 4, 2], [2, 7, 6]], 
                                          [[1, 3, 0], [0, 3, 2], [3, 7, 2]], 
                                          [[4, 1, 0], [2, 4, 0], [5, 1, 4], [6, 4, 2], [6, 5, 4]], 
                                          [[5, 1, 4], [5, 7, 1], [6, 5, 4], [7, 5, 6]], 
                                          [[6, 4, 2], [2, 7, 6], [6, 5, 4], [7, 5, 6]], 
                                          [[5, 7, 1], [3, 7, 2], [2, 7, 6], [7, 5, 6]]]
        all_one_ring_triangles = self.boundary_vertex_checker._BoundaryVertexChecker__get_all_one_ring_triangles(self.mesh)
        for idx, one_ring_triangles in enumerate(all_one_ring_triangles):
            correct_one_ring_triangles = set(map(tuple, correct_all_one_ring_triangles[idx]))
            one_ring_triangles = set(map(tuple, one_ring_triangles))
            self.assertTrue(not(correct_one_ring_triangles.difference(one_ring_triangles)))
                
    def test_if_vertex_not_boundary_vertex_then_should_be_false(self):
        self.assertFalse(self.boundary_vertex_checker.is_boundary_vertex([-0.5, -0.5, -0.5]))
        
    def test_if_vertex_is_boundary_vertex_then_should_be_true(self):
        self.assertTrue(self.boundary_vertex_checker.is_boundary_vertex([-0.5, -0.5, 0.5]))
        
unittest.main(argv=[''], verbosity=2, exit=False)

test_get_one_ring_triangles_should_get_whole_vertex_related_triangles (__main__.BoundaryVertexCheckerTest) ... ok
test_get_one_ring_vertices_should_get_whole_vertex_neighbors (__main__.BoundaryVertexCheckerTest) ... ok
test_if_vertex_is_boundary_vertex_then_should_be_true (__main__.BoundaryVertexCheckerTest) ... ok
test_if_vertex_not_boundary_vertex_then_should_be_false (__main__.BoundaryVertexCheckerTest) ... ok
test_if_has_5_1_ring_edges_return_edge_list (__main__.BoundaryVertexTest) ... ok
test_if_has_5_1_ring_triangles_return_triangle_list (__main__.BoundaryVertexTest) ... ok

----------------------------------------------------------------------
Ran 6 tests in 0.010s

OK


# Feature Selection

In [32]:
#select m points from the face
m = 100 
def select_m_points(mesh, m=100):
    #randomly generate m points index
    selected_index = []
    iter_time = 0
    vertices = mesh.vertices
    while(len(selected_index)<m and iter_time<10000):
        random_index = random.randint(0, len(vertices)-1)
        if is_maintain_distance(vertices[random_index], vertices[selected_index], 20):
            selected_index.append(random_index)
        iter_time+=1
    
    #draw the points on mesh
    print("length of selected: ", len(selected_index))
    visual_selected_points(mesh, selected_index)
    return vertices[selected_index]

def count_distance(p1, p2):
    return np.power(np.sum(np.square(p1 - p2)), 0.5)

def is_maintain_distance(point, selected_points, distance):
    for selected_point in selected_points:
        if collections.Counter(point) == collections.Counter(selected_point):
            continue
        elif count_distance(point, selected_point) < distance:
            #print(count_distance(point, selected_point))
            return False
    return True

def visual_selected_points(mesh, selected_index, selected_color=[255,0,0,0],
                          not_selected_color=[0,255,0,0]):
    # unite the color of points on face
    for index, vertex_color in enumerate(mesh.visual.vertex_colors):
        if index in selected_index:
            mesh.visual.vertex_colors[index] =  selected_color
        else:
            mesh.visual.vertex_colors[index] = not_selected_color


In [33]:
selected_points = select_m_points(mesh, m=400)
mesh.show()

length of selected:  400
